看看均线策略。

In [1]:
import pandas as pd
from datetime import datetime
import trdb2py

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

我们测测BTC，特定的时间段来分析吧。

In [13]:
# 具体基金
asset = 'bitmex.XBTUSD|1h'

# 起始时间，0表示从最开始算起
# tsStart = 0
tsStart = int(trdb2py.str2timestamp('2020-01-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
# tsEnd = -1
tsEnd = int(trdb2py.str2timestamp('2020-09-01', '%Y-%m-%d'))

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

首先看看这个基金的基准表现，就是在开始时间就直接买入，然后一直持有，看具体的收益率。

In [14]:
# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='baseline',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaseline, dtFormat='%Y-%m-%d %H:%M:%S', toImg=isStaticImg, width=width, height=height)

那么策略基准线大概就是这样了。

我们可以基本看到，其实BTC价格波动没那么大，基本上也就是上下10%左右，但BTC特殊的是，会在短时间内出现剧烈的波动

接下来，测一下均线

In [19]:
lstparams = []

for ema in range(168, 169):    
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['upcross'],
        strVals=['ema.{}'.format(ema)],
    )
    
    buy1 = trdb2py.trading2_pb2.CtrlCondition(
        name='waittostart',
        vals=[ema],
    )    
            
    sell0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['downcross'],
        strVals=['ema.{}'.format(ema)],
    )
    
    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )

    s0.buy.extend([buy0, buy1])
    s0.sell.extend([sell0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell) 
    s0.paramsInit.CopyFrom(paramsinit)        
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='ema{}'.format(ema),
    ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=2)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], dtFormat='%Y-%m-%d %H:%M:%S', toImg=isStaticImg, width=width, height=height)

In [5]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 1]

dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
12  baseline     0.176046       2020-05-08     2020-05-10      1.814864   
1      ema57     0.161057       2020-05-14     2020-07-21      1.437919   
2      ema56     0.166711       2020-05-14     2020-07-21      1.426063   
11     ema60     0.165244       2020-05-14     2020-07-21      1.423754   
0      ema58     0.166937       2020-05-14     2020-07-21      1.406691   
10     ema59     0.179543       2020-05-14     2020-07-21      1.402661   
3      ema55     0.173119       2020-05-14     2020-07-21      1.379995   
4      ema54     0.179408       2020-05-14     2020-07-21      1.355420   
8      ema50     0.161120       2020-05-14     2020-07-21      1.348455   
7      ema51     0.162358       2020-05-14     2020-07-21      1.341069   
5      ema53     0.179915       2020-05-14     2020-07-21      1.327736   
6      ema52     0.180823       2020-05-14     2020-07-21      1.326801   
9      ema49     0.171616       2020-05-14     2020-07-21      1.306798   

      sharpe  annualizedReturns  annualizedVolatility  variance  
12  2.100301           0.815086              0.373797  0.052966  
1   1.462723           0.438038              0.278958  0.020260  
2   1.420482           0.426179              0.278905  0.019521  
11  1.407979           0.423870              0.279741  0.018448  
0   1.352019           0.406801              0.278695  0.018108  
10  1.333391           0.402771              0.279566  0.017464  
3   1.255995           0.380099              0.278742  0.016530  
4   1.168203           0.355517              0.278647  0.014976  
8   1.143134           0.348549              0.278663  0.015707  
7   1.116525           0.341162              0.278688  0.015462  
5   1.069148           0.327826              0.278563  0.014250  
6   1.065815           0.326890              0.278557  0.014213  
9   0.993444           0.306882              0.278709  0.013148

可以看到，简单的均线策略，完全不适用于BTC，几乎是完败。

不知道是本身数据时间粒度太小还是别的原因。

BTC 5m的数据，简单的均线几乎完败，1h会好一些，但也不是太好

我的分析是，btc会有短期内的大调整，如果5m的数据，就是几个5m区间内的剧烈变动，如果把分钟数据过滤掉，拿1h的数据来看，会发现又有几小时的剧烈变化，就是这种小的剧烈变化，造成均线粒度过小时，抓不住趋势，过大时，很难从下跌里逃出来，最终还是抓不住趋势。

In [23]:
lstparams = []

for ema0 in range(11, 21):
    for ema1 in range(120, 121):
        buy0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['upcross'],
            strVals=['ema.{}'.format(ema0)],
        )

        buy1 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema0],
        )
        
        buy2 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['up'],
            strVals=['ema.{}'.format(ema1)],
        )
        
        buy3 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema1],
        )        

        sell0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['downcross'],
            strVals=['ema.{}'.format(ema0)],
        )

        s0 = trdb2py.trading2_pb2.Strategy(
            name="normal",
            asset=trdb2py.str2asset(asset),
        )

        s0.buy.extend([buy0, buy1, buy2, buy3])
        s0.sell.extend([sell0])
        s0.paramsBuy.CopyFrom(paramsbuy)
        s0.paramsSell.CopyFrom(paramssell) 
        s0.paramsInit.CopyFrom(paramsinit)        
        lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
            assets=[trdb2py.str2asset(asset)],
            startTs=tsStart,
            endTs=tsEnd,
            strategies=[s0],
            title='ema{}&ema{}'.format(ema0, ema1),
        ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=3)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], dtFormat='%Y-%m-%d %H:%M:%S', toImg=isStaticImg, width=width, height=height)

In [9]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 1]

dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
12     baseline     0.176046       2020-05-08     2020-05-10      1.814864   
4   ema60&ema54     0.162361       2020-05-14     2020-07-21      1.440233   
3   ema60&ema55     0.165836       2020-05-14     2020-07-21      1.430640   
2   ema60&ema56     0.166442       2020-05-14     2020-07-21      1.425191   
1   ema60&ema57     0.166442       2020-05-14     2020-07-21      1.424588   
11  ema60&ema60     0.165244       2020-05-14     2020-07-21      1.423754   
0   ema60&ema58     0.171789       2020-05-14     2020-07-21      1.412786   
10  ema60&ema59     0.171789       2020-05-14     2020-07-21      1.412786   
9   ema60&ema49     0.163967       2020-04-30     2020-07-21      1.354318   
8   ema60&ema50     0.172189       2020-04-30     2020-07-21      1.342891   
6   ema60&ema52     0.173095       2020-04-30     2020-07-21      1.341420   
7   ema60&ema51     0.173095       2020-04-30     2020-07-21      1.341420   
5   ema60&ema53     0.174892       2020-04-30     2020-07-21      1.338506   

      sharpe  annualizedReturns  annualizedVolatility  variance  
12  2.100301           0.815086              0.373797  0.052966  
4   1.536119           0.440352              0.267136  0.019629  
3   1.499970           0.430757              0.267177  0.018856  
2   1.476593           0.425307              0.267715  0.018392  
1   1.474338           0.424704              0.267716  0.018374  
11  1.407979           0.423870              0.279741  0.018448  
0   1.429888           0.412899              0.267782  0.017628  
10  1.429888           0.412899              0.267782  0.017628  
9   1.278912           0.354415              0.253664  0.012786  
8   1.228977           0.342984              0.254671  0.011976  
6   1.223040           0.341513              0.254704  0.011894  
7   1.223040           0.341513              0.254704  0.011894  
5   1.211547           0.338598              0.254714  0.011743

在btc上单独看均线，我怀疑很难出现好的效果，原因就是我上面提到的，至少是日内，会出现短时间内的剧烈变化，均线无法将上涨全部吃掉，把下跌跳过，可以考虑试试日线